# TMF String tester  
## Relation between string amplitude and driving frequency
In this experiments the string is driven with an electromagnet with various ascending frequency sweeps. The string length is changing between the experiments. The goal of this experiment is to confirm the relation between the resonant frequency of the string and its length.  
The resonant frequency of the string can be calculated with this formula:  
$$f_{0}=\frac{v}{\lambda}$$
Where $f_{0}$ is the resonant frequency, $v$ is the wave speed and $\lambda$ is the wavelength. This implies that there will be inverse proportion between the resonant frequency and the wavelength.  
The wavelength is $\lambda=2L$ because we are working with the 1st harmonic resonant frequency.

In [5]:
import numpy as np
import pandas as pd

from scipy.optimize import curve_fit

import plotly.express as px

filenames = ['length_f0_50cm_18N_processed.csv', 'length_f0_51cm_18N_processed.csv', 'length_f0_52cm_18N_processed.csv',
             'length_f0_53cm_18N_processed.csv', 'length_f0_54cm_18N_processed.csv', 'length_f0_55cm_18N_processed.csv',
             'length_f0_56cm_18N_processed.csv', 'length_f0_57cm_18N_processed.csv', 'length_f0_58cm_18N_processed.csv',
             'length_f0_59cm_18N_processed.csv', 'length_f0_60cm_18N_processed.csv', 'length_f0_61cm_18N_processed.csv',
             'length_f0_62cm_18N_processed.csv', 'length_f0_63cm_18N_processed.csv', 'length_f0_64cm_18N_processed.csv']

lengths = [50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64]

titles = ['Frequency vs. Amplitude(50cm)', 'Frequency vs. Amplitude(51cm)', 'Frequency vs. Amplitude(52cm)',
          'Frequency vs. Amplitude(53cm)', 'Frequency vs. Amplitude(54cm)', 'Frequency vs. Amplitude(55cm)',
          'Frequency vs. Amplitude(56cm)', 'Frequency vs. Amplitude(57cm)', 'Frequency vs. Amplitude(58cm)',
          'Frequency vs. Amplitude(59cm)', 'Frequency vs. Amplitude(60cm)', 'Frequency vs. Amplitude(61cm)',
          'Frequency vs. Amplitude(62cm)', 'Frequency vs. Amplitude(63cm)', 'Frequency vs. Amplitude(64cm)']

Firstly we need to read the measured data.

In [6]:
data = []

# Read data files.
for filename in filenames:
    file = pd.read_csv('data/' + filename)
    data.append(file[1:])

Now we need to process the data for plotting. We are averaging the plotted value from 100 sensor readings.

In [7]:
plot_data = []

for i, experiment in enumerate(data):
    plot_data.append([])
    for j in range(0, len(experiment), 100):
        try:
            plot_data[i].append(
                {
                    'frequency': experiment['frequency'][j], 
                    'displacement_y': np.mean(np.abs(experiment[j:j+100]['y_val']))
                }
            )
        except Exception:
            pass
    
    plot_data[i] = pd.DataFrame(plot_data[i])


Here we are creating a dataframe with the lengths and resonant frequencies. Resonant frequencies are found based on the string amplitude - it is biggest when the driving frequency matches the resonant frequency

In [8]:
length_f0 = {'length': [], 'resonant_frequency': []}

for i, experiment in enumerate(plot_data):
    length_f0['length'].append(lengths[i])
    min_val = experiment['displacement_y'].idxmax()
    length_f0['resonant_frequency'].append(experiment['frequency'][min_val])

length_f0 = pd.DataFrame(length_f0)

In [5]:
for i in range(len(plot_data)):
    fig = px.line(plot_data[i], x=plot_data[i]['frequency'], y=plot_data[i]['displacement_y'], title=titles[i])
    fig.show()

We are using 3 functions for fitting:
1. Quadratic function: $y=ax^{2}+bx+c$
2. Linear function: $y=ax+b$
3. Hyperbolic function: $y=\frac{a}{x}+b$

In [9]:
length_f0

length  resonant_frequency
0       50           52.334501
1       51           51.582695
2       52           50.962311
3       53           49.407348
4       54           49.231731
5       55           47.770250
6       56           47.015622
7       57           45.865915
8       58           45.159161
9       59           43.961049
10      60           43.782942
11      61           43.204878
12      62           42.495963
13      63           42.184432
14      64           41.077622

In [59]:
fit_function = lambda x, a: ((19.5 / 0.0071) ** 0.5) / (x * 10 ** -2 * 2)

In [60]:
fit_params, pcov = curve_fit(fit_function, length_f0['length'], length_f0['resonant_frequency'])

In [56]:
fit_params

array([1.])

Here we are calculating the function errors.

In [61]:
error = np.linalg.norm(length_f0['resonant_frequency'] - fit_function(length_f0['length'], *fit_params))

print(error)

1.2850573354009507


In [65]:
import plotly.graph_objects as go

trace1 = go.Scatter(
    x = length_f0['length'],
    y = length_f0['resonant_frequency'],
    error_x=dict(
        type='constant',
        value=0.05,
        visible=True
    ),
    error_y=dict(
        type='constant',
        value=0.119,
        visible=True
    ),
    mode = 'markers',
    name = 'data'
)

trace2 = go.Scatter(
    x = length_f0['length'],
    y = fit_function(length_f0['length'], *fit_params),
    mode = 'lines',
    name = 'sqrt(T / μ) / 2x'
)

graph_data = [trace1, trace2]
layout = dict(
    title = 'Length vs. resonant frequency',
    xaxis = dict(title='length (cm)'),
    yaxis = dict(title='frequency (Hz)')
)

fig = go.Figure(
    data = graph_data,
    layout = layout
)

fig.show()

# Results:
- The best function fit was hyperbolic function - function of inverse proportion
- We have proven the inverse proportion of resonant frequency $f_{0}$ and the wavelength $\lambda=2L$